In [1]:
import random
import numpy as np
import matplotlib.pyplot as plt
import math
from datetime import datetime, timedelta
from scipy.stats import poisson
from random import randrange
import pandas as pd


In [5]:
class PoissonGenerator:
    """
    Generate transactions timestamps list. Current version works with milliseconds.
    """
    
    def __init__(self, cycle_size: int, mean_occurencies: float):
        """
        Create a Poisson generator
        
        Keyword_arguments:
        cycle_size (int) -- reviewable cycle size in milliseconds
        mean_occurencies (float) -- mean amount of transactions
            happening in given cycle size
        """
        self.cycle_size = cycle_size
        self.mean_occurencies = mean_occurencies
        self.cumulative_probabilities = 0
        
        
    def __generate_poisson_outcome__(self) -> int:
        """
        Generate how many transactions will happen, considering cycle size 
        and mean transaction amount
        """
        return np.random.poisson(self.mean_occurencies, 1)[0]
    
    
    def generate_transactions(self, current_timestamp: datetime) -> list:
        """
        Generate array of transactions timestamps, considering Poisson distribution and
        random distribution of timestamps in given cycle size
        
        Keyword_arguments:
        current_timestamp (datetime) -- reviewable cycle starting point
        """
        transactions_timestamps = []
        current_transaction_count = self.__generate_poisson_outcome__()
        
        for i in range(current_transaction_count):
            transactions_timestamps.append(current_timestamp + timedelta(milliseconds=randrange(self.cycle_size)))
        
        return transactions_timestamps
    

In [4]:
class NormalGenerator:
    """
    Generate transaction values conform normal distribution
    """
    
    def __init__(self, mu: float=0, sigma: float=0):
        """
        Create a normal distribution generator
        
        Keyword_arguments:
        mu (float) -- mean transaction price (default 0.0)
        sigma (float) -- standard deviation of transaction price (default 0.0)
        """
        self.mu = mu
        self.sigma = sigma
      
    
    def reset_params(self, mu: float, sigma: float):
        """
        Change parameters of existing generator
        
        Keyword_arguments:
        mu (float) -- mean transaction price (default 0.0)
        sigma (float) -- standard deviation of transaction price (default 0.0)
        """
        self.mu = mu
        self.sigma = sigma
    

    def generate_transactions(self, transactions_count: int) -> list:
        """
        Generate transaction prices list considering mu and sigma
        
        Keyword_arguments:
        transactions_count (int) -- required transactions count
        """
        return np.random.normal(self.mu, self.sigma, transactions_count)


In [5]:
class Transaction:
    def __init__(self, id: int, timestamp: datetime, value: float):
        self.id = id
        self.timestamp = timestamp
        self.value = value
        
    
    def to_string(self) -> str:
        return str('Transaction {id = ' + str(self.id) + ', timestamp = "' + str(self.timestamp) + '", value = ' + str(self.value)) + '}'

In [6]:
class MonteCarloTransactionSimulator:
    """
    Monte Carlo transactions generator, that generates transactions frequency using Poisson 
    distribution and transaction values using normal distribution (time metrics - milliseconds)
    """
    def __init__(
        self, transaction_density_generator: PoissonGenerator, transaction_values_generator: NormalGenerator, 
        first_currency: str, second_currency: str
    ):
        """
        Create a Monte-Carlo transaction simulator
        
        Keyword_arguments:
        transaction_density_generator (PoissonGenerator) -- Poisson transaction distribution generator
        transaction_values_generator (NormalGenerator) -- Normal transaction distribution generator
        """
        self.transaction_density_generator = transaction_density_generator
        self.transaction_values_generator = transaction_values_generator
        self.first_currency = first_currency
        self.second_currency = second_currency
        self.transaction_history = []
        
    
    def reset_values_generator_params(self, mu: float, sigma: float):
        """
        Change parameters of existing values (normal distribution) generator
        
        Keyword_arguments:
        mu (float) -- mean transaction price (default 0.0)
        sigma (float) -- standard deviation of transaction price (default 0.0)
        """
        self.transaction_density_generator.reset_params(mu, sigma)
        
        
    def clear_transaction_history(self):
        """
        Clear all records from transaction history
        """
        self.transaction_history.clear()
    
    
    def generate_transactions(self, current_timestamp: datetime):
        """
        Generates transactions list with timestamps and values assigned to 
        
        Keyword arguments:
        current_timestamp (datetime) -- initial datetime point from where cycle will be reviewed
        """
        # generate timestamps (and sort them) and generate transaction values
        timestamps = self.transaction_density_generator.generate_transactions(current_timestamp)
        timestamps.sort()
        values = self.transaction_values_generator.generate_transactions(len(timestamps))
        
        # create transactions, appending them to the transaction history
        for index in range(len(timestamps)):
            new_transaction = Transaction(index, timestamps[index], values[index])
            self.transaction_history.append(new_transaction)
            
            
    def transaction_history_to_csv(self, filename: str):
        """
        Write transaction history to specified .csv file
        
        Keyword arguments:
        filename (str) -- name of .csv file where to write data
        """
        # form empty dataframe
        transaction_history_dataframe = pd.DataFrame(columns=['id', 'FirstCurrency', 'SecondCurrency', 'Timestamp', 'Value'])
        
        # append all new records to the dataframe
        for index in range(len(self.transaction_history)):
            new_row = {
                'id': self.transaction_history[index].id, 
                'FirstCurrency': self.first_currency, 
                'SecondCurrency': self.second_currency, 
                'Timestamp': self.transaction_history[index].timestamp,
                'Value': self.transaction_history[index].value
            }
            transaction_history_dataframe = transaction_history_dataframe.append(new_row, ignore_index=True)
        
        # if there is such file -> append new records to it, otherwise create a new file from existing table
        try:
            with open(filename) as f:
                transaction_history_dataframe.to_csv(filename, mode='a', header=False)
        except IOError:
            transaction_history_dataframe.to_csv(filename)

In [7]:
# example of creating simulation
simulator = MonteCarloTransactionSimulator(
    PoissonGenerator(cycle_size=60000, mean_occurencies=5), 
    NormalGenerator(mu=10, sigma=5), 'ETH', 'DAI'
)

#  set starting point to be as current timestamp and then start loop, where after each iteration 
# reviewable timestamp will be updated by shifting it further conform generator cycle size
current_iteration_timestamp = datetime.now()
for index in range(60*24*7):
    simulator.generate_transactions(current_iteration_timestamp)
    current_iteration_timestamp += timedelta(milliseconds=randrange(simulator.transaction_density_generator.cycle_size))

# show all generated transactions
for index in range(len(simulator.transaction_history)):
    print(simulator.transaction_history[index].to_string())
    
# write all generated transactions (entire generated transaction history) to csv file
simulator.transaction_history_to_csv('history.csv')

Transaction {id = 0, timestamp = "2021-10-20 19:36:51.763027", value = 4.837989976416951}
Transaction {id = 1, timestamp = "2021-10-20 19:36:59.180027", value = 8.719074070742433}
Transaction {id = 0, timestamp = "2021-10-20 19:36:19.960027", value = 14.581509081327484}
Transaction {id = 1, timestamp = "2021-10-20 19:36:25.943027", value = 7.078544592015448}
Transaction {id = 2, timestamp = "2021-10-20 19:36:33.095027", value = 13.052873483989401}
Transaction {id = 3, timestamp = "2021-10-20 19:37:08.357027", value = 9.117143296241855}
Transaction {id = 0, timestamp = "2021-10-20 19:36:42.975027", value = 17.54026526222947}
Transaction {id = 1, timestamp = "2021-10-20 19:36:50.945027", value = 10.934650840460234}
Transaction {id = 2, timestamp = "2021-10-20 19:37:18.190027", value = 4.771385098228701}
Transaction {id = 3, timestamp = "2021-10-20 19:37:21.132027", value = -0.3280027706096824}
Transaction {id = 4, timestamp = "2021-10-20 19:37:26.840027", value = 10.376810562392217}
Tran

KeyboardInterrupt: 

# Next version of the generator, applying additional details to the generator work principle

In [8]:
class NormalDeviationFactorGenerator:
    """
    Generate deviation coefficient factor of the actual price from AMM-estimated one
    """
    
    def __init__(self, matching_coefficient: float=1, deviation_factor: float=0):
        """
        Create a normal distribution generator
        
        Keyword_arguments:
        matching_coefficient (float) -- how AMM price matches with actual price
            on price at the moment of transaction execution (default 1.0)
        deviation_factor (float) -- standard deviation of the matching coefficient
            (default 0.0)
        """
        self.matching_coefficient = matching_coefficient
        self.deviation_factor = deviation_factor
      
    
    def reset_params(self, matching_coefficient: float, deviation_factor: float):
        """
        Change parameters of existing generator
        
        Keyword_arguments:
        matching_coefficient (float) -- how AMM price matches with actual price
            on price at the moment of transaction execution (default 1.0)
        deviation_factor (float) -- standard deviation of the matching coefficient
            (default 0.0)
        """
        self.matching_coefficient = matching_coefficient
        self.deviation_factor = deviation_factor


    def generate_transaction_multiplier(self) -> float:
        """
        Generate transaction multiplier for current transaction conform mean
        matching coefficient and deviation factor
        """
        return np.random.normal(self.matching_coefficient, self.deviation_factor, 1)[0]



deviation_generator = NormalDeviationFactorGenerator(matching_coefficient=1, deviation_factor=0.01)
for index in range(100):
    print(str(100 * deviation_generator.generate_transaction_multiplier()))


100.08918867564375
100.4529545080057
100.63613145049611
100.56005918083358
101.10610553025106
99.77524109485121
99.05996122784804
101.12297067058742
100.33163681972086
97.8214340759541
98.8306173351622
99.246473582989
99.63165753856063
100.13190285165538
99.51345241670313
100.71100578197667
99.33087778041502
97.93489374984632
100.59088816958545
100.07458154971556
99.51265536349932
101.56101237777196
100.61593757403011
99.70467792934255
99.26691241444749
99.84647684910591
101.01981621741585
99.66981772707868
98.82724123206901
100.28324176199632
99.89747341704407
101.05614139123227
99.38257448062333
101.70554127893506
98.58556352543523
101.09228564021977
98.24006095146277
101.80308146948813
98.96927518510593
100.14967822436105
98.26664027698249
101.63361061427503
100.4947253147866
98.41397265053088
99.53019922489126
99.2286814240689
98.6352892903677
101.42182788937639
100.24954439607691
99.80844310670844
100.35384506010307
101.5265123431954
99.59956317341391
99.89441111734621
99.26465275

# cooperation with Dima

In [1]:
import random
import numpy as np
import matplotlib.pyplot as plt
import math
from datetime import datetime, timedelta
from scipy.stats import poisson
from random import randrange
import pandas as pd


class PoissonGenerator:
    """
    Generate transactions timestamps list. Current version works with milliseconds.
    """
    
    def __init__(self, cycle_size: int, mean_occurencies: float):
        """
        Create a Poisson generator
        
        Keyword_arguments:
        cycle_size (int) -- reviewable cycle size in milliseconds
        mean_occurencies (float) -- mean amount of transactions
            happening in given cycle size
        """
        self.cycle_size = cycle_size
        self.mean_occurencies = mean_occurencies
        self.cumulative_probabilities = 0
        
        
    def __generate_poisson_outcome__(self) -> int:
        """
        Generate how many transactions will happen, considering cycle size 
        and mean transaction amount
        """
        return np.random.poisson(self.mean_occurencies, 1)[0]
    
    
    def generate_transactions(self, current_timestamp: datetime) -> list:
        """
        Generate array of transactions timestamps, considering Poisson distribution and
        random distribution of timestamps in given cycle size
        
        Keyword_arguments:
        current_timestamp (datetime) -- reviewable cycle starting point
        """
        transactions_timestamps = []
        current_transaction_count = self.__generate_poisson_outcome__()
        
        for i in range(current_transaction_count):
            transactions_timestamps.append(current_timestamp + timedelta(milliseconds=randrange(self.cycle_size)))
        
        return transactions_timestamps
    


class NormalGenerator:
    """
    Generate transaction values conform normal distribution
    """
    
    def __init__(self, mu: float=0, sigma: float=0):
        """
        Create a normal distribution generator
        
        Keyword_arguments:
        mu (float) -- mean transaction price (default 0.0)
        sigma (float) -- standard deviation of transaction price (default 0.0)
        """
        self.mu = mu
        self.sigma = sigma
      
    
    def reset_params(self, mu: float, sigma: float):
        """
        Change parameters of existing generator
        
        Keyword_arguments:
        mu (float) -- mean transaction price (default 0.0)
        sigma (float) -- standard deviation of transaction price (default 0.0)
        """
        self.mu = mu
        self.sigma = sigma
    

    def generate_transactions(self, transactions_count: int) -> list:
        """
        Generate transaction prices list considering mu and sigma
        
        Keyword_arguments:
        transactions_count (int) -- required transactions count
        """
        return np.random.normal(self.mu, self.sigma, transactions_count)



class Transaction:
    """
    Class with information regarding swapping transaction
    """
    def __init__(self, timestamp: datetime, 
                token_in_amount: float, token_in: str, 
                token_out: str, 
                slope: float=0.05):
        self.datetime_timestamp = timestamp
        self.token_in = token_in
        self.token_in_amount = token_in_amount
        self.token_out = token_out
        self.token_out_amount = None
        self.slope = slope



    def set_token_out_amount(self, token_out_amount: float):
        self.token_out_amount = token_out_amount
        
    
    def to_string(self) -> str:
        """
        form a string that can be used for showing information on console
        """
        return str(
            'Transaction {datetime timestamp = ' + str(self.datetime_timestamp) + 
            ', token in amount = "' + str(self.token_in_amount) + 
            '", token in name = ' + str(self.token_in) + 
            ', token out amount = ' + str(self.token_out_amount) + 
            ', token out name = ' + str(self.token_out) + 
            ', slope = ' + str(self.slope) + '}'
        )

In [2]:
class MonteCarloTransactionSimulator:
    """
    Monte Carlo transactions generator, that generates transactions frequency using Poisson 
    distribution and transaction values using normal distribution (time metrics - milliseconds)
    """
    def __init__(
        self, frequency_generator: PoissonGenerator, token_in_generator: NormalGenerator, 
        first_currency: str, second_currency: str
    ):
        """
        Create a Monte-Carlo transaction simulator
        
        Keyword_arguments:
        frequency_generator (PoissonGenerator) -- Poisson transaction distribution generator
        token_in_generator (NormalGenerator) -- Normal transaction distribution generator
        first_currency -- name of the first token in transaction
        second_currency -- name of the second token in transaction
        """
        self.frequency_generator = frequency_generator
        self.token_in_generator = token_in_generator
        self.first_currency = first_currency
        self.second_currency = second_currency
        self.transaction_history = []
        
    
    def reset_values_generator_params(self, mu: float, sigma: float):
        """
        Change parameters of existing values (normal distribution) generator
        
        Keyword_arguments:
        mu (float) -- mean transaction price (default 0.0)
        sigma (float) -- standard deviation of transaction price (default 0.0)
        """
        self.frequency_generator.reset_params(mu, sigma)
        
        
    def clear_transaction_history(self):
        """
        Clear all records from transaction history
        """
        self.transaction_history.clear()
    
    
    def generate_transactions(self, current_timestamp: datetime):
        """
        Generates transactions list with timestamps and token_in values. All transactions are recorded
        to the 'transaction_history' variable.
        
        Keyword arguments:
        current_timestamp (datetime) -- initial datetime point from where cycle will be reviewed
        current_amm_coef (float) -- current AMM market coefficient that defines price of out
            token relative to in token
        """
        # generate timestamps and token_in values
        timestamps = self.frequency_generator.generate_transactions(current_timestamp)
        timestamps.sort()
        token_in_values = self.token_in_generator.generate_transactions(len(timestamps))
        
        # form new transactions and record them into 'transaction history' variable
        for index in range(len(timestamps)):
            new_transaction = Transaction(
                timestamp=timestamps[index], 
                token_in_amount=token_in_values[index], 
                token_in=self.first_currency,
                token_out=self.second_currency
            )
            self.transaction_history.append(new_transaction)


    def get_history(self) -> list:
        """
        Get transaction history
        """
        return self.transaction_history
            
            
    def transaction_history_to_csv(self, filename: str):
        """
        Write transaction history to specified .csv file
        
        Keyword arguments:
        filename (str) -- name of .csv file where to write data
        """
        # form empty dataframe
        transaction_history_dataframe = pd.DataFrame(columns=[
            'datetime_timestamp', 'TokenIn', 'TokenInAmount', 'TokenOut', 'TokenOutAmount', 'Slope'
        ])
        
        # append all new records to the dataframe
        for index in range(len(self.transaction_history)):
            new_row = {
                'datetime_timestamp': self.transaction_history[index].datetime_timestamp,
                'TokenIn': self.transaction_history[index].token_in,
                'TokenInAmount': self.transaction_history[index].token_in_amount, 
                'TokenOut': self.transaction_history[index].token_out,
                'TokenOutAmount': self.transaction_history[index].token_out_amount,
                'Slope': self.transaction_history[index].slope
            }
            transaction_history_dataframe = transaction_history_dataframe.append(new_row, ignore_index=True)
        
        # either append new records to the existing file, or create a new one from existing table
        try:
            with open(filename) as f:
                transaction_history_dataframe.to_csv(filename, mode='a', header=False)
        except IOError:
            transaction_history_dataframe.to_csv(filename)

In [4]:
# create simulator with specifying parameters of the normal distribution for token_in
# value estimation and Poisson distribution for transaction frequency estimation
simulator = MonteCarloTransactionSimulator(
    PoissonGenerator(cycle_size=60000, mean_occurencies=500), 
    NormalGenerator(mu=10, sigma=5), 'ETH', 'DAI'
)

# set current timestamp as starting point and start loop, where each iteration shifts reviewable
# timestamp further conform simulator cycle size
current_iteration_timestamp = datetime.now()
for index in range(60*24*7):
    simulator.generate_transactions(current_iteration_timestamp)
    current_iteration_timestamp += timedelta(milliseconds=randrange(simulator.frequency_generator.cycle_size))

# show generated transactions history
# for index in range(len(simulator.transaction_history)):
#     print(simulator.transaction_history[index].to_string())
    
# write generated transactions history to csv file
# simulator.transaction_history_to_csv('history.csv')

In [5]:
simulator.transaction_history

 ...]